# My office in Toronto

Diego is considering creating a software development venture for which he is looking in Toronto for a suitable place to install the administrative office since the developers work from home, keeping in mind the needs that this office may need, a recommendation is expected as to neighborhoods where can normally operate this office

In [1]:
import requests
import pandas as pd
import numpy as np

Waiting for a Spark session to start...
Waiting for a Spark session to start...
Spark Initialization Done! ApplicationId = app-20200323193102-0001
KERNEL_ID = a5bf142b-9c32-4e1c-9fb8-64180654fdb4
Spark Initialization Done! ApplicationId = app-20200323193102-0001
KERNEL_ID = a5bf142b-9c32-4e1c-9fb8-64180654fdb4


In [2]:
post_codes_ca_url = requests.get('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M').text

In [3]:
# Get the data from Wikipedia page
from bs4 import BeautifulSoup
soup = BeautifulSoup(post_codes_ca_url,'lxml')

In [4]:

source = requests.get('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M').text

soup = BeautifulSoup(source, 'html5lib')

postal_codes_dict = {} # initialize an empty dictionary to save the data in
for table_cell in soup.find_all('td'):
    try:
        postal_code = table_cell.p.b.text # get the postal code
        postal_code_investigate = table_cell.span.text
        neighborhoods_data = table_cell.span.text # get the rest of the data in the cell
        borough = neighborhoods_data.split('(')[0] # get the borough in the cell
        
        # if the cell is not assigned then ignore it
        if neighborhoods_data == 'Not assigned':
            neighborhoods = []
        # else process the data and add it to the dictionary
        else:
            postal_codes_dict[postal_code] = {}
            
            try:
                neighborhoods = neighborhoods_data.split('(')[1]
            
                # remove parantheses from neighborhoods string
                neighborhoods = neighborhoods.replace('(', ' ')
                neighborhoods = neighborhoods.replace(')', ' ')

                neighborhoods_names = neighborhoods.split('/')
                neighborhoods_clean = ', '.join([name.strip() for name in neighborhoods_names])
            except:
                borough = borough.strip('\n')
                neighborhoods_clean = borough
 
            # add borough and neighborhood to dictionary
            postal_codes_dict[postal_code]['borough'] = borough
            postal_codes_dict[postal_code]['neighborhoods'] = neighborhoods_clean
    except:
        pass
    
# create an empty dataframe
columns = ['PostalCode', 'Borough', 'Neighborhood']
toronto_df = pd.DataFrame(columns=columns)
toronto_df

# populate dataframe with data from dictionary
for ind, postal_code in enumerate(postal_codes_dict):
    borough = postal_codes_dict[postal_code]['borough']
    neighborhood = postal_codes_dict[postal_code]['neighborhoods']
    toronto_df = toronto_df.append({"PostalCode": postal_code, 
                                        "Borough": borough, 
                                        "Neighborhood": neighborhood},
                                        ignore_index=True)

# print number of rows of dataframe
toronto_df.shape[0]
toronto_df

PostalCode                                            Borough  \
0          M3A                                         North York   
1          M4A                                         North York   
2          M5A                                   Downtown Toronto   
3          M6A                                         North York   
4          M7A       Queen's Park / Ontario Provincial Government   
..         ...                                                ...   
98         M8X                                          Etobicoke   
99         M4Y                                   Downtown Toronto   
100        M7Y  East TorontoBusiness reply mail Processing Cen...   
101        M8Y                                          Etobicoke   
102        M8Z                                          Etobicoke   

                                          Neighborhood  
0                                            Parkwoods  
1                                     Victoria Village  
2                            Regent Park, Harbourfront  
3                     Lawrence Manor, Lawrence Heights  
4         Queen's Park / Ontario Provincial Government  
..                                                 ...  
98       The Kingsway, Montgomery Road, Old Mill North  
99                                Church and Wellesley  
100                                     Enclave of M4L  
101  Old Mill South, King's Mill Park, Sunnylea, Hu...  
102  Mimico NW, The Queensway West, South of Bloor,...  

[103 rows x 3 columns]

PostalCode                                            Borough  \
0          M3A                                         North York   
1          M4A                                         North York   
2          M5A                                   Downtown Toronto   
3          M6A                                         North York   
4          M7A       Queen's Park / Ontario Provincial Government   
..         ...                                                ...   
98         M8X                                          Etobicoke   
99         M4Y                                   Downtown Toronto   
100        M7Y  East TorontoBusiness reply mail Processing Cen...   
101        M8Y                                          Etobicoke   
102        M8Z                                          Etobicoke   

                                          Neighborhood  
0                                            Parkwoods  
1                                     Victoria Village  
2                            Regent Park, Harbourfront  
3                     Lawrence Manor, Lawrence Heights  
4         Queen's Park / Ontario Provincial Government  
..                                                 ...  
98       The Kingsway, Montgomery Road, Old Mill North  
99                                Church and Wellesley  
100                                     Enclave of M4L  
101  Old Mill South, King's Mill Park, Sunnylea, Hu...  
102  Mimico NW, The Queensway West, South of Bloor,...  

[103 rows x 3 columns]

In [5]:
# get all geographical coordinates of the neighborhoods.
geo_data_df = pd.read_csv('https://cocl.us/Geospatial_data')
geo_data_df

Postal Code   Latitude  Longitude
0           M1B  43.806686 -79.194353
1           M1C  43.784535 -79.160497
2           M1E  43.763573 -79.188711
3           M1G  43.770992 -79.216917
4           M1H  43.773136 -79.239476
..          ...        ...        ...
98          M9N  43.706876 -79.518188
99          M9P  43.696319 -79.532242
100         M9R  43.688905 -79.554724
101         M9V  43.739416 -79.588437
102         M9W  43.706748 -79.594054

[103 rows x 3 columns]

Postal Code   Latitude  Longitude
0           M1B  43.806686 -79.194353
1           M1C  43.784535 -79.160497
2           M1E  43.763573 -79.188711
3           M1G  43.770992 -79.216917
4           M1H  43.773136 -79.239476
..          ...        ...        ...
98          M9N  43.706876 -79.518188
99          M9P  43.696319 -79.532242
100         M9R  43.688905 -79.554724
101         M9V  43.739416 -79.588437
102         M9W  43.706748 -79.594054

[103 rows x 3 columns]

In [6]:
geo_data_df = geo_data_df.rename({'Postal Code':'PostalCode'}, axis=1)

In [7]:
# Merge the coordinates info in Postalcode/Borough/Neighborhood dataframe.
merged_df = pd.merge(toronto_df,geo_data_df, on='PostalCode')

merged_df

PostalCode                                            Borough  \
0          M3A                                         North York   
1          M4A                                         North York   
2          M5A                                   Downtown Toronto   
3          M6A                                         North York   
4          M7A       Queen's Park / Ontario Provincial Government   
..         ...                                                ...   
98         M8X                                          Etobicoke   
99         M4Y                                   Downtown Toronto   
100        M7Y  East TorontoBusiness reply mail Processing Cen...   
101        M8Y                                          Etobicoke   
102        M8Z                                          Etobicoke   

                                          Neighborhood   Latitude  Longitude  
0                                            Parkwoods  43.753259 -79.329656  
1                                     Victoria Village  43.725882 -79.315572  
2                            Regent Park, Harbourfront  43.654260 -79.360636  
3                     Lawrence Manor, Lawrence Heights  43.718518 -79.464763  
4         Queen's Park / Ontario Provincial Government  43.662301 -79.389494  
..                                                 ...        ...        ...  
98       The Kingsway, Montgomery Road, Old Mill North  43.653654 -79.506944  
99                                Church and Wellesley  43.665860 -79.383160  
100                                     Enclave of M4L  43.662744 -79.321558  
101  Old Mill South, King's Mill Park, Sunnylea, Hu...  43.636258 -79.498509  
102  Mimico NW, The Queensway West, South of Bloor,...  43.628841 -79.520999  

[103 rows x 5 columns]

PostalCode                                            Borough  \
0          M3A                                         North York   
1          M4A                                         North York   
2          M5A                                   Downtown Toronto   
3          M6A                                         North York   
4          M7A       Queen's Park / Ontario Provincial Government   
..         ...                                                ...   
98         M8X                                          Etobicoke   
99         M4Y                                   Downtown Toronto   
100        M7Y  East TorontoBusiness reply mail Processing Cen...   
101        M8Y                                          Etobicoke   
102        M8Z                                          Etobicoke   

                                          Neighborhood   Latitude  Longitude  
0                                            Parkwoods  43.753259 -79.329656  
1                                     Victoria Village  43.725882 -79.315572  
2                            Regent Park, Harbourfront  43.654260 -79.360636  
3                     Lawrence Manor, Lawrence Heights  43.718518 -79.464763  
4         Queen's Park / Ontario Provincial Government  43.662301 -79.389494  
..                                                 ...        ...        ...  
98       The Kingsway, Montgomery Road, Old Mill North  43.653654 -79.506944  
99                                Church and Wellesley  43.665860 -79.383160  
100                                     Enclave of M4L  43.662744 -79.321558  
101  Old Mill South, King's Mill Park, Sunnylea, Hu...  43.636258 -79.498509  
102  Mimico NW, The Queensway West, South of Bloor,...  43.628841 -79.520999  

[103 rows x 5 columns]

In [8]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes  
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes 
import folium # map rendering library

print('Libraries imported.')

Solving environment: done
Solving environment: done
done

# All requested packages already installed.


# All requested packages already installed.

Solving environment: done
Solving environment: done
done

# All requested packages already installed.


# All requested packages already installed.

Libraries imported.
Libraries imported.


In [9]:
address = 'Toronto, ON'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

/opt/ibm/conda/miniconda3.6/lib/python3.6/site-packages/ipykernel/__main__.py:3: DeprecationWarning: Using Nominatim with the default "geopy/1.21.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  app.launch_new_instance()
/opt/ibm/conda/miniconda3.6/lib/python3.6/site-packages/ipykernel/__main__.py:3: DeprecationWarning: Using Nominatim with the default "geopy/1.21.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by ov

The geograpical coordinate of Toronto are 43.653963, -79.387207.
The geograpical coordinate of Toronto are 43.653963, -79.387207.


In [10]:
# create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(merged_df['Latitude'], merged_df['Longitude'], merged_df['Borough'], merged_df['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

In [11]:
# Define Foursquare Credentials and Version
CLIENT_ID = '10NRDSRO2X3D0FP3SV0DTUHZE3NM424AEU4XPRV2WMPC0V3G' # your Foursquare ID
CLIENT_SECRET = 'FEWC4V2P4X0ZCFXYBF1LUCNOMIOBF5ZYQROJ44W4DKJTDEL4' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 10NRDSRO2X3D0FP3SV0DTUHZE3NM424AEU4XPRV2WMPC0V3G
CLIENT_SECRET:FEWC4V2P4X0ZCFXYBF1LUCNOMIOBF5ZYQROJ44W4DKJTDEL4
Your credentails:
CLIENT_ID: 10NRDSRO2X3D0FP3SV0DTUHZE3NM424AEU4XPRV2WMPC0V3G
CLIENT_SECRET:FEWC4V2P4X0ZCFXYBF1LUCNOMIOBF5ZYQROJ44W4DKJTDEL4


In [12]:
# Plan to explore the Neighborhood 'Christie' where is at downtown Toronto, get its index first. 
merged_df[merged_df['Neighborhood']=='Christie'].index

Int64Index([25], dtype='int64')

Int64Index([25], dtype='int64')

In [13]:
neighborhood_latitude = merged_df.loc[75, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = merged_df.loc[75, 'Longitude'] # neighborhood longitude value

neighborhood_name = merged_df.loc[75, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Parkdale, Roncesvalles are 43.6489597, -79.456325.
Latitude and longitude values of Parkdale, Roncesvalles are 43.6489597, -79.456325.


In [14]:
LIMIT = 350
radius = 500
url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, radius, LIMIT)

In [15]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5e790d6c40a7ea001b28d500'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Bay Street Corridor',
  'headerFullLocation': 'Bay Street Corridor, Toronto',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 74,
  'suggestedBounds': {'ne': {'lat': 43.6584630045, 'lng': -79.38099903084075},
   'sw': {'lat': 43.649462995499995, 'lng': -79.39341496915925}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '5227bb01498e17bf485e6202',
       'name': 'Downtown Toronto',
       'location': {'lat': 43.65323167517444,
        'lng': -79.38529600606677,
        'labeledLatLngs': [{'label': 'display',
          'lat': 43.65323167517444,
          

{'meta': {'code': 200, 'requestId': '5e790d6c40a7ea001b28d500'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Bay Street Corridor',
  'headerFullLocation': 'Bay Street Corridor, Toronto',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 74,
  'suggestedBounds': {'ne': {'lat': 43.6584630045, 'lng': -79.38099903084075},
   'sw': {'lat': 43.649462995499995, 'lng': -79.39341496915925}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '5227bb01498e17bf485e6202',
       'name': 'Downtown Toronto',
       'location': {'lat': 43.65323167517444,
        'lng': -79.38529600606677,
        'labeledLatLngs': [{'label': 'display',
          'lat': 43.65323167517444,
          

In [16]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [17]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

/opt/ibm/conda/miniconda3.6/lib/python3.6/site-packages/ipykernel/__main__.py:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  app.launch_new_instance()
/opt/ibm/conda/miniconda3.6/lib/python3.6/site-packages/ipykernel/__main__.py:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  app.launch_new_instance()


name           categories        lat        lng
0    Downtown Toronto         Neighborhood  43.653232 -79.385296
1             Japango     Sushi Restaurant  43.655268 -79.385165
2           Poke Guys           Poke Place  43.654895 -79.385052
3          Rolltation  Japanese Restaurant  43.654918 -79.387424
4  Sansotei Ramen 三草亭     Ramen Restaurant  43.655157 -79.386501

name           categories        lat        lng
0    Downtown Toronto         Neighborhood  43.653232 -79.385296
1             Japango     Sushi Restaurant  43.655268 -79.385165
2           Poke Guys           Poke Place  43.654895 -79.385052
3          Rolltation  Japanese Restaurant  43.654918 -79.387424
4  Sansotei Ramen 三草亭     Ramen Restaurant  43.655157 -79.386501

In [18]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

74 venues were returned by Foursquare.
74 venues were returned by Foursquare.


In [19]:
# create a function to repeat the same process to all the neighborhoods in Toronto

def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [20]:
# find the venues in all Toronto Neighbohoods
toronto_venues = getNearbyVenues(names=merged_df['Neighborhood'],
                                   latitudes=merged_df['Latitude'],
                                   longitudes=merged_df['Longitude']
                                  )

Parkwoods
Parkwoods
Victoria Village
Regent Park, Harbourfront
Victoria Village
Regent Park, Harbourfront
Lawrence Manor, Lawrence Heights
Lawrence Manor, Lawrence Heights
Queen's Park / Ontario Provincial Government
Queen's Park / Ontario Provincial Government
Islington Avenue
Malvern, Rouge
Islington Avenue
Malvern, Rouge
Don Mills North
Parkview Hill, Woodbine Gardens
Don Mills North
Parkview Hill, Woodbine Gardens
Garden District, Ryerson
Garden District, Ryerson
Glencairn
West Deane Park, Princess Gardens, Martin Grove, Islington, Cloverdale
Glencairn
West Deane Park, Princess Gardens, Martin Grove, Islington, Cloverdale
Rouge Hill, Port Union, Highland Creek
Don Mills South
Rouge Hill, Port Union, Highland Creek
Don Mills South
Woodbine Heights
St. James Town
Woodbine Heights
St. James Town
Humewood-Cedarvale
Eringate, Bloordale Gardens, Old Burnhamthorpe, Markland Wood
Humewood-Cedarvale
Eringate, Bloordale Gardens, Old Burnhamthorpe, Markland Wood
Guildwood, Morningside, West H

In [21]:
print(toronto_venues.shape)
toronto_venues.head()

(2226, 7)
(2226, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2  Victoria Village              43.725882              -79.315572   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

                    Venue  Venue Latitude  Venue Longitude  \
0         Brookbanks Park       43.751976       -79.332140   
1           Variety Store       43.751974       -79.333114   
2  Victoria Village Arena       43.723481       -79.315635   
3             Tim Hortons       43.725517       -79.313103   
4               Portugril       43.725819       -79.312785   

          Venue Category  
0                   Park  
1      Food & Drink Shop  
2           Hockey Arena  
3            Coffee Shop  
4  Portuguese Restaurant

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2  Victoria Village              43.725882              -79.315572   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

                    Venue  Venue Latitude  Venue Longitude  \
0         Brookbanks Park       43.751976       -79.332140   
1           Variety Store       43.751974       -79.333114   
2  Victoria Village Arena       43.723481       -79.315635   
3             Tim Hortons       43.725517       -79.313103   
4               Portugril       43.725819       -79.312785   

          Venue Category  
0                   Park  
1      Food & Drink Shop  
2           Hockey Arena  
3            Coffee Shop  
4  Portuguese Restaurant

In [22]:
# check how many venues were returned for each neighborhood
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Agincourt                                                               5   
Alderwood, Long Branch                                                  9   
Bathurst Manor, Wilson Heights, Downsview North                        19   
Bayview Village                                                         4   
Bedford Park, Lawrence Manor East                                      25   
Berczy Park                                                            55   
Birch Cliff, Cliffside West                                             4   
Brockton, Parkdale Village, Exhibition Place                           22   
CN Tower, King and Spadina, Railway Lands, Harb...                     14   
Caledonia-Fairbanks                                                     4   
Cedarbrae                                                               8   
Central Bay Street                                                     81   
Christie                                                               17   
Church and Wellesley                                                   88   
Clairville, Humberwood, Woodbine Downs, West Hu...                      2   
Clarks Corners, Tam O'Shanter, Sullivan                                14   
Cliffside, Cliffcrest, Scarborough Village West                         4   
Commerce Court, Victoria Hotel                                        100   
Davisville                                                             35   
Davisville North                                                        8   
Del Ray, Mount Dennis, Keelsdale and Silverthorn                        4   
Don Mills North                                                         5   
Don Mills South                                                        23   
Dorset Park, Wexford Heights, Scarborough Town ...                      5   
Downsview Central                                                       4   
Downsview East                                                          2   
Downsview Northwest                                                     4   
Downsview West                                                          6   
Dufferin, Dovercourt Village                                           19   
Enclave of L4W                                                         13   
Enclave of M4L                                                         15   
Enclave of M5E                                                         95   
Eringate, Bloordale Gardens, Old Burnhamthorpe,...                      9   
Fairview, Henry Farm, Oriole                                           68   
First Canadian Place, Underground city                                100   
Forest Hill North & West                                                4   
Garden District, Ryerson                                              100   
Glencairn                                                               4   
Golden Mile, Clairlea, Oakridge                                        10   
Guildwood, Morningside, West Hill                                       7   
Harbourfront East, Union Station, Toronto Islands                     100   
High Park, The Junction South                                          23   
Hillcrest Village                                                       4   
Humber Summit                                                           3   
Humberlea, Emery                                                        2   
Humewood-Cedarvale                                                      4   
India Bazaar, The Beaches West                                         18   
Kennedy Park, Ionview, East Birchmount Park                             6   
Kensington Market, Chinatown, Grange Park                              89   
Kingsview Village, St. Phillips, Martin Grove G...                      3   
Lawrence Manor, Lawrence Heights                

Neighborhood Latitude  \
Neighborhood                                                                
Agincourt                                                               5   
Alderwood, Long Branch                                                  9   
Bathurst Manor, Wilson Heights, Downsview North                        19   
Bayview Village                                                         4   
Bedford Park, Lawrence Manor East                                      25   
Berczy Park                                                            55   
Birch Cliff, Cliffside West                                             4   
Brockton, Parkdale Village, Exhibition Place                           22   
CN Tower, King and Spadina, Railway Lands, Harb...                     14   
Caledonia-Fairbanks                                                     4   
Cedarbrae                                                               8   
Central Bay Street                                                     81   
Christie                                                               17   
Church and Wellesley                                                   88   
Clairville, Humberwood, Woodbine Downs, West Hu...                      2   
Clarks Corners, Tam O'Shanter, Sullivan                                14   
Cliffside, Cliffcrest, Scarborough Village West                         4   
Commerce Court, Victoria Hotel                                        100   
Davisville                                                             35   
Davisville North                                                        8   
Del Ray, Mount Dennis, Keelsdale and Silverthorn                        4   
Don Mills North                                                         5   
Don Mills South                                                        23   
Dorset Park, Wexford Heights, Scarborough Town ...                      5   
Downsview Central                                                       4   
Downsview East                                                          2   
Downsview Northwest                                                     4   
Downsview West                                                          6   
Dufferin, Dovercourt Village                                           19   
Enclave of L4W                                                         13   
Enclave of M4L                                                         15   
Enclave of M5E                                                         95   
Eringate, Bloordale Gardens, Old Burnhamthorpe,...                      9   
Fairview, Henry Farm, Oriole                                           68   
First Canadian Place, Underground city                                100   
Forest Hill North & West                                                4   
Garden District, Ryerson                                              100   
Glencairn                                                               4   
Golden Mile, Clairlea, Oakridge                                        10   
Guildwood, Morningside, West Hill                                       7   
Harbourfront East, Union Station, Toronto Islands                     100   
High Park, The Junction South                                          23   
Hillcrest Village                                                       4   
Humber Summit                                                           3   
Humberlea, Emery                                                        2   
Humewood-Cedarvale                                                      4   
India Bazaar, The Beaches West                                         18   
Kennedy Park, Ionview, East Birchmount Park                             6   
Kensington Market, Chinatown, Grange Park                              89   
Kingsview Village, St. Phillips, Martin Grove G...                      3   
Lawrence Manor, Lawrence Heights                

In [23]:
# find out how many unique categories can be curated from all the returned venues
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 273 uniques categories.
There are 273 uniques categories.


In [24]:
# Analyze Each Neighborhood

# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
column_list = toronto_onehot.columns.tolist()
column_number = int(column_list.index('Neighborhood'))
column_list = [column_list[column_number]] + column_list[:column_number] + column_list[column_number+1:]
toronto_onehot = toronto_onehot[column_list]

toronto_onehot.head()

Neighborhood  Accessories Store  Afghan Restaurant  Airport  \
0         Parkwoods                  0                  0        0   
1         Parkwoods                  0                  0        0   
2  Victoria Village                  0                  0        0   
3  Victoria Village                  0                  0        0   
4  Victoria Village                  0                  0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0                 0                    0             0         0            0   
1                 0                    0             0         0            0   
2                 0                    0             0         0            0   
3                 0                    0             0         0            0   
4                 0                    0             0         0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0           0                    0                 0                   0   
1           0                    0                 0                   0   
2           0                    0                 0                   0   
3           0                    0                 0                   0   
4           0                    0                 0                   0   

   Auto Garage  Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0            0              0          0           0           0       0   
1            0              0          0           0           0       0   
2            0              0          0           0           0       0   
3            0              0          0           0           0       0   
4            0              0          0           0           0       0   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Stadium  Beach  \
0     0    0               0                 0                   0      0   
1     0    0               0                 0                   0      0   
2     0    0               0                 0                   0      0   
3     0    0               0                 0                   0      0   
4     0    0               0                 0                   0      0   

   Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  Bike Shop  \
0                0         0           0                   0          0   
1                0         0           0                   0          0   
2                0         0           0                   0          0   
3                0         0           0                   0          0   
4                0         0           0                   0          0   

   Bistro  Board Shop  Boat or Ferry  Bookstore  Boutique  \
0       0           0              0          0         0   
1       0           0              0          0         0   
2       0           0              0          0         0   
3       0           0              0          0         0   
4       0           0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                     0               0        0            0   

   Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \
0        

Neighborhood  Accessories Store  Afghan Restaurant  Airport  \
0         Parkwoods                  0                  0        0   
1         Parkwoods                  0                  0        0   
2  Victoria Village                  0                  0        0   
3  Victoria Village                  0                  0        0   
4  Victoria Village                  0                  0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0                 0                    0             0         0            0   
1                 0                    0             0         0            0   
2                 0                    0             0         0            0   
3                 0                    0             0         0            0   
4                 0                    0             0         0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0           0                    0                 0                   0   
1           0                    0                 0                   0   
2           0                    0                 0                   0   
3           0                    0                 0                   0   
4           0                    0                 0                   0   

   Auto Garage  Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0            0              0          0           0           0       0   
1            0              0          0           0           0       0   
2            0              0          0           0           0       0   
3            0              0          0           0           0       0   
4            0              0          0           0           0       0   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Stadium  Beach  \
0     0    0               0                 0                   0      0   
1     0    0               0                 0                   0      0   
2     0    0               0                 0                   0      0   
3     0    0               0                 0                   0      0   
4     0    0               0                 0                   0      0   

   Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  Bike Shop  \
0                0         0           0                   0          0   
1                0         0           0                   0          0   
2                0         0           0                   0          0   
3                0         0           0                   0          0   
4                0         0           0                   0          0   

   Bistro  Board Shop  Boat or Ferry  Bookstore  Boutique  \
0       0           0              0          0         0   
1       0           0              0          0         0   
2       0           0              0          0         0   
3       0           0              0          0         0   
4       0           0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                     0               0        0            0   

   Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \
0        

In [25]:
toronto_onehot.shape

(2226, 273)

(2226, 273)

In [26]:
# group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  Accessories Store  \
0                                           Agincourt           0.000000   
1                              Alderwood, Long Branch           0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North           0.000000   
3                                     Bayview Village           0.000000   
4                   Bedford Park, Lawrence Manor East           0.000000   
5                                         Berczy Park           0.000000   
6                         Birch Cliff, Cliffside West           0.000000   
7        Brockton, Parkdale Village, Exhibition Place           0.000000   
8   CN Tower, King and Spadina, Railway Lands, Har...           0.000000   
9                                 Caledonia-Fairbanks           0.000000   
10                                          Cedarbrae           0.000000   
11                                 Central Bay Street           0.000000   
12                                           Christie           0.000000   
13                               Church and Wellesley           0.000000   
14  Clairville, Humberwood, Woodbine Downs, West H...           0.000000   
15            Clarks Corners, Tam O'Shanter, Sullivan           0.000000   
16    Cliffside, Cliffcrest, Scarborough Village West           0.000000   
17                     Commerce Court, Victoria Hotel           0.000000   
18                                         Davisville           0.000000   
19                                   Davisville North           0.000000   
20   Del Ray, Mount Dennis, Keelsdale and Silverthorn           0.000000   
21                                    Don Mills North           0.000000   
22                                    Don Mills South           0.000000   
23  Dorset Park, Wexford Heights, Scarborough Town...           0.000000   
24                                  Downsview Central           0.000000   
25                                     Downsview East           0.000000   
26                                Downsview Northwest           0.000000   
27                                     Downsview West           0.000000   
28                       Dufferin, Dovercourt Village           0.000000   
29                                     Enclave of L4W           0.000000   
30                                     Enclave of M4L           0.000000   
31                                     Enclave of M5E           0.000000   
32  Eringate, Bloordale Gardens, Old Burnhamthorpe...           0.000000   
33                       Fairview, Henry Farm, Oriole           0.000000   
34             First Canadian Place, Underground city           0.000000   
35                           Forest Hill North & West           0.000000   
36                           Garden District, Ryerson           0.000000   
37                                          Glencairn           0.000000   
38                    Golden Mile, Clairlea, Oakridge           0.000000   
39                  Guildwood, Morningside, West Hill           0.000000   
40  Harbourfront East, Union Station, Toronto Islands           0.000000   
41                      High Park, The Junction South           0.000000   
42                                  Hillcrest Village           0.000000   
43                                      Humber Summit           0.000000   
44                                   Humberlea, Emery           0.000000   
45                                 Humewood-Cedarvale           0.000000   
46                     India Bazaar, The Beaches West           0.000000   
47        Kennedy Park, Ionview, East Birchmount Park           0.000000   
48          Kensington Market, Chinatown, Grange Park           0.000000   
49  Kingsview Village, St. Phillips, Martin Grove ...           0.000000   
50                   Lawrence Manor, Lawrence Heights           0.153846   
51                                      Lawrence Park           0.000000   
52           

Neighborhood  Accessories Store  \
0                                           Agincourt           0.000000   
1                              Alderwood, Long Branch           0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North           0.000000   
3                                     Bayview Village           0.000000   
4                   Bedford Park, Lawrence Manor East           0.000000   
5                                         Berczy Park           0.000000   
6                         Birch Cliff, Cliffside West           0.000000   
7        Brockton, Parkdale Village, Exhibition Place           0.000000   
8   CN Tower, King and Spadina, Railway Lands, Har...           0.000000   
9                                 Caledonia-Fairbanks           0.000000   
10                                          Cedarbrae           0.000000   
11                                 Central Bay Street           0.000000   
12                                           Christie           0.000000   
13                               Church and Wellesley           0.000000   
14  Clairville, Humberwood, Woodbine Downs, West H...           0.000000   
15            Clarks Corners, Tam O'Shanter, Sullivan           0.000000   
16    Cliffside, Cliffcrest, Scarborough Village West           0.000000   
17                     Commerce Court, Victoria Hotel           0.000000   
18                                         Davisville           0.000000   
19                                   Davisville North           0.000000   
20   Del Ray, Mount Dennis, Keelsdale and Silverthorn           0.000000   
21                                    Don Mills North           0.000000   
22                                    Don Mills South           0.000000   
23  Dorset Park, Wexford Heights, Scarborough Town...           0.000000   
24                                  Downsview Central           0.000000   
25                                     Downsview East           0.000000   
26                                Downsview Northwest           0.000000   
27                                     Downsview West           0.000000   
28                       Dufferin, Dovercourt Village           0.000000   
29                                     Enclave of L4W           0.000000   
30                                     Enclave of M4L           0.000000   
31                                     Enclave of M5E           0.000000   
32  Eringate, Bloordale Gardens, Old Burnhamthorpe...           0.000000   
33                       Fairview, Henry Farm, Oriole           0.000000   
34             First Canadian Place, Underground city           0.000000   
35                           Forest Hill North & West           0.000000   
36                           Garden District, Ryerson           0.000000   
37                                          Glencairn           0.000000   
38                    Golden Mile, Clairlea, Oakridge           0.000000   
39                  Guildwood, Morningside, West Hill           0.000000   
40  Harbourfront East, Union Station, Toronto Islands           0.000000   
41                      High Park, The Junction South           0.000000   
42                                  Hillcrest Village           0.000000   
43                                      Humber Summit           0.000000   
44                                   Humberlea, Emery           0.000000   
45                                 Humewood-Cedarvale           0.000000   
46                     India Bazaar, The Beaches West           0.000000   
47        Kennedy Park, Ionview, East Birchmount Park           0.000000   
48          Kensington Market, Chinatown, Grange Park           0.000000   
49  Kingsview Village, St. Phillips, Martin Grove ...           0.000000   
50                   Lawrence Manor, Lawrence Heights           0.153846   
51                                      Lawrence Park           0.000000   
52           

In [27]:
toronto_grouped.shape

(100, 273)

(100, 273)

In [28]:
# print each neighborhood along with the top 10 most common venues

num_top_venues = 10

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Agincourt----
                       venue  freq
0             Clothing Store   0.2
1  Latin American Restaurant   0.2
2               Skating Rink   0.2
3             Breakfast Spot   0.2
4                     Lounge   0.2
5             Medical Center   0.0
6  Middle Eastern Restaurant   0.0
7         Mexican Restaurant   0.0
8              Metro Station   0.0
9                Men's Store   0.0


----Alderwood, Long Branch----
                venue  freq
0         Pizza Place  0.22
1                 Gym  0.11
2                Pool  0.11
3        Skating Rink  0.11
4            Pharmacy  0.11
5         Coffee Shop  0.11
6                 Pub  0.11
7      Sandwich Place  0.11
8  Mexican Restaurant  0.00
9       Metro Station  0.00


----Bathurst Manor, Wilson Heights, Downsview North----
                       venue  freq
0                       Bank  0.11
1                Coffee Shop  0.11
2  Middle Eastern Restaurant  0.05
3                 Restaurant  0.05
4                Gas St

In [29]:
# put that into a pandas dataframe
## First, write a function to sort the venues in descending order.

def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [30]:
# create the new dataframe and display the top 10 venues for each neighborhood.

num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{}  Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th  Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted

Neighborhood  \
0                                           Agincourt   
1                              Alderwood, Long Branch   
2     Bathurst Manor, Wilson Heights, Downsview North   
3                                     Bayview Village   
4                   Bedford Park, Lawrence Manor East   
5                                         Berczy Park   
6                         Birch Cliff, Cliffside West   
7        Brockton, Parkdale Village, Exhibition Place   
8   CN Tower, King and Spadina, Railway Lands, Har...   
9                                 Caledonia-Fairbanks   
10                                          Cedarbrae   
11                                 Central Bay Street   
12                                           Christie   
13                               Church and Wellesley   
14  Clairville, Humberwood, Woodbine Downs, West H...   
15            Clarks Corners, Tam O'Shanter, Sullivan   
16    Cliffside, Cliffcrest, Scarborough Village West   
17                     Commerce Court, Victoria Hotel   
18                                         Davisville   
19                                   Davisville North   
20   Del Ray, Mount Dennis, Keelsdale and Silverthorn   
21                                    Don Mills North   
22                                    Don Mills South   
23  Dorset Park, Wexford Heights, Scarborough Town...   
24                                  Downsview Central   
25                                     Downsview East   
26                                Downsview Northwest   
27                                     Downsview West   
28                       Dufferin, Dovercourt Village   
29                                     Enclave of L4W   
30                                     Enclave of M4L   
31                                     Enclave of M5E   
32  Eringate, Bloordale Gardens, Old Burnhamthorpe...   
33                       Fairview, Henry Farm, Oriole   
34             First Canadian Place, Underground city   
35                           Forest Hill North & West   
36                           Garden District, Ryerson   
37                                          Glencairn   
38                    Golden Mile, Clairlea, Oakridge   
39                  Guildwood, Morningside, West Hill   
40  Harbourfront East, Union Station, Toronto Islands   
41                      High Park, The Junction South   
42                                  Hillcrest Village   
43                                      Humber Summit   
44                                   Humberlea, Emery   
45                                 Humewood-Cedarvale   
46                     India Bazaar, The Beaches West   
47        Kennedy Park, Ionview, East Birchmount Park   
48          Kensington Market, Chinatown, Grange Park   
49  Kingsview Village, St. Phillips, Martin Grove ...   
50                   Lawrence Manor, Lawrence Heights   
51                                      Lawrence Park   
52                                            Leaside   
53                           Little Portugal, Trinity   
54                                     Malvern, Rouge   
55  Milliken, Agincourt North, Steeles East, L'Amo...   
56  Mimico NW, The Queensway West, South of Bloor,...   
57                        Moore Park, Summerhill East   
58       New Toronto, Mimico South, Humber Bay Shores   
59           North Park, Maple Leaf Park, Upwood Park   
60                                 North Toronto West   
61                    Northwood Park, York University   
62  Old Mill South, King's Mill Park, Sunnylea, Hu...   
63                             Parkdale, Roncesvalles   
64                    Parkview Hill, Woodbine Gardens   
65                                          Parkwoods   
66       Queen's Park / Ontario Provincial Government   
67                          Regent Park, Harbourfront   
68                           Richmond, Adelaide, King   
69                                           Roseda

Neighborhood  \
0                                           Agincourt   
1                              Alderwood, Long Branch   
2     Bathurst Manor, Wilson Heights, Downsview North   
3                                     Bayview Village   
4                   Bedford Park, Lawrence Manor East   
5                                         Berczy Park   
6                         Birch Cliff, Cliffside West   
7        Brockton, Parkdale Village, Exhibition Place   
8   CN Tower, King and Spadina, Railway Lands, Har...   
9                                 Caledonia-Fairbanks   
10                                          Cedarbrae   
11                                 Central Bay Street   
12                                           Christie   
13                               Church and Wellesley   
14  Clairville, Humberwood, Woodbine Downs, West H...   
15            Clarks Corners, Tam O'Shanter, Sullivan   
16    Cliffside, Cliffcrest, Scarborough Village West   
17                     Commerce Court, Victoria Hotel   
18                                         Davisville   
19                                   Davisville North   
20   Del Ray, Mount Dennis, Keelsdale and Silverthorn   
21                                    Don Mills North   
22                                    Don Mills South   
23  Dorset Park, Wexford Heights, Scarborough Town...   
24                                  Downsview Central   
25                                     Downsview East   
26                                Downsview Northwest   
27                                     Downsview West   
28                       Dufferin, Dovercourt Village   
29                                     Enclave of L4W   
30                                     Enclave of M4L   
31                                     Enclave of M5E   
32  Eringate, Bloordale Gardens, Old Burnhamthorpe...   
33                       Fairview, Henry Farm, Oriole   
34             First Canadian Place, Underground city   
35                           Forest Hill North & West   
36                           Garden District, Ryerson   
37                                          Glencairn   
38                    Golden Mile, Clairlea, Oakridge   
39                  Guildwood, Morningside, West Hill   
40  Harbourfront East, Union Station, Toronto Islands   
41                      High Park, The Junction South   
42                                  Hillcrest Village   
43                                      Humber Summit   
44                                   Humberlea, Emery   
45                                 Humewood-Cedarvale   
46                     India Bazaar, The Beaches West   
47        Kennedy Park, Ionview, East Birchmount Park   
48          Kensington Market, Chinatown, Grange Park   
49  Kingsview Village, St. Phillips, Martin Grove ...   
50                   Lawrence Manor, Lawrence Heights   
51                                      Lawrence Park   
52                                            Leaside   
53                           Little Portugal, Trinity   
54                                     Malvern, Rouge   
55  Milliken, Agincourt North, Steeles East, L'Amo...   
56  Mimico NW, The Queensway West, South of Bloor,...   
57                        Moore Park, Summerhill East   
58       New Toronto, Mimico South, Humber Bay Shores   
59           North Park, Maple Leaf Park, Upwood Park   
60                                 North Toronto West   
61                    Northwood Park, York University   
62  Old Mill South, King's Mill Park, Sunnylea, Hu...   
63                             Parkdale, Roncesvalles   
64                    Parkview Hill, Woodbine Gardens   
65                                          Parkwoods   
66       Queen's Park / Ontario Provincial Government   
67                          Regent Park, Harbourfront   
68                           Richmond, Adelaide, King   
69                                           Roseda

In [31]:
# Cluster Neighborhoods
## Run k-means to cluster the neighborhood into 5 clusters.

# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 0], dtype=int32)

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 0], dtype=int32)

In [32]:
# add clustering labels
toronto_merged = merged_df.head(100)
toronto_merged['Cluster Labels'] = kmeans.labels_

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

toronto_merged.head()

/opt/ibm/conda/miniconda3.6/lib/python3.6/site-packages/ipykernel/__main__.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  app.launch_new_instance()


PostalCode                                       Borough  \
0        M3A                                    North York   
1        M4A                                    North York   
2        M5A                              Downtown Toronto   
3        M6A                                    North York   
4        M7A  Queen's Park / Ontario Provincial Government   

                                   Neighborhood   Latitude  Longitude  \
0                                     Parkwoods  43.753259 -79.329656   
1                              Victoria Village  43.725882 -79.315572   
2                     Regent Park, Harbourfront  43.654260 -79.360636   
3              Lawrence Manor, Lawrence Heights  43.718518 -79.464763   
4  Queen's Park / Ontario Provincial Government  43.662301 -79.389494   

   Cluster Labels 1st  Common Venue           2nd  Common Venue  \
0               1              Park           Food & Drink Shop   
1               1       Coffee Shop  Financial or Legal Service   
2               1       Coffee Shop                      Bakery   
3               1    Clothing Store           Accessories Store   
4               1       Coffee Shop                        Park   

       3rd  Common Venue 4th  Common Venue 5th  Common Venue  \
0    Distribution Center  Department Store      Dessert Shop   
1  Portuguese Restaurant      Hockey Arena       Yoga Studio   
2                    Pub              Park           Theater   
3               Boutique       Event Space        Shoe Store   
4                   Bank          Beer Bar          Boutique   

        6th  Common Venue   7th  Common Venue   8th  Common Venue  \
0      Dim Sum Restaurant               Diner      Discount Store   
1     Distribution Center        Dessert Shop  Dim Sum Restaurant   
2              Restaurant                Café  Mexican Restaurant   
3  Furniture / Home Store  Miscellaneous Shop         Coffee Shop   
4      Seafood Restaurant      Sandwich Place        Burger Joint   

       9th  Common Venue    10th  Common Venue  
0                Dog Run  Ethiopian Restaurant  
1                  Diner        Discount Store  
2            Event Space        Chocolate Shop  
3  Vietnamese Restaurant          Concert Hall  
4             Restaurant         Burrito Place

/opt/ibm/conda/miniconda3.6/lib/python3.6/site-packages/ipykernel/__main__.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  app.launch_new_instance()


PostalCode                                       Borough  \
0        M3A                                    North York   
1        M4A                                    North York   
2        M5A                              Downtown Toronto   
3        M6A                                    North York   
4        M7A  Queen's Park / Ontario Provincial Government   

                                   Neighborhood   Latitude  Longitude  \
0                                     Parkwoods  43.753259 -79.329656   
1                              Victoria Village  43.725882 -79.315572   
2                     Regent Park, Harbourfront  43.654260 -79.360636   
3              Lawrence Manor, Lawrence Heights  43.718518 -79.464763   
4  Queen's Park / Ontario Provincial Government  43.662301 -79.389494   

   Cluster Labels 1st  Common Venue           2nd  Common Venue  \
0               1              Park           Food & Drink Shop   
1               1       Coffee Shop  Financial or Legal Service   
2               1       Coffee Shop                      Bakery   
3               1    Clothing Store           Accessories Store   
4               1       Coffee Shop                        Park   

       3rd  Common Venue 4th  Common Venue 5th  Common Venue  \
0    Distribution Center  Department Store      Dessert Shop   
1  Portuguese Restaurant      Hockey Arena       Yoga Studio   
2                    Pub              Park           Theater   
3               Boutique       Event Space        Shoe Store   
4                   Bank          Beer Bar          Boutique   

        6th  Common Venue   7th  Common Venue   8th  Common Venue  \
0      Dim Sum Restaurant               Diner      Discount Store   
1     Distribution Center        Dessert Shop  Dim Sum Restaurant   
2              Restaurant                Café  Mexican Restaurant   
3  Furniture / Home Store  Miscellaneous Shop         Coffee Shop   
4      Seafood Restaurant      Sandwich Place        Burger Joint   

       9th  Common Venue    10th  Common Venue  
0                Dog Run  Ethiopian Restaurant  
1                  Diner        Discount Store  
2            Event Space        Chocolate Shop  
3  Vietnamese Restaurant          Concert Hall  
4             Restaurant         Burrito Place

In [33]:
# create final map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=10)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [34]:
# Examine Clusters

## Cluster 1
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels  \
9                                 Downtown Toronto               0   
25                                Downtown Toronto               0   
35                           East YorkEast Toronto               0   
37                                    West Toronto               0   
49                                      North York               0   
51                                     Scarborough               0   
55                                      North York               0   
57                                      North York               0   
59                                      North York               0   
65                                     Scarborough               0   
69                                    West Toronto               0   
83                                 Central Toronto               0   
85                                     Scarborough               0   
92  Downtown TorontoStn A PO Boxes25 The Esplanade               0   
98                                       Etobicoke               0   

         1st  Common Venue   2nd  Common Venue           3rd  Common Venue  \
9              Coffee Shop      Clothing Store                        Café   
25           Grocery Store                Café                        Park   
35                    Park   Convenience Store               Metro Station   
37                     Bar         Coffee Shop                  Restaurant   
49                    Park              Bakery  Construction & Landscaping   
51     American Restaurant       Movie Theater                Skating Rink   
55      Italian Restaurant         Coffee Shop                  Restaurant   
57  Furniture / Home Store      Baseball Field                 Yoga Studio   
59        Ramen Restaurant         Coffee Shop                 Pizza Place   
65       Indian Restaurant           Pet Store       Vietnamese Restaurant   
69                     Bar                Café          Mexican Restaurant   
83                     Gym                Park                Tennis Court   
85                    Park              Bakery                 Coffee Shop   
92             Coffee Shop  Seafood Restaurant                  Restaurant   
98                   River                Park                     Dog Run   

     4th  Common Venue    5th  Common Venue          6th  Common Venue  \
9       Cosmetics Shop  Japanese Restaurant  Middle Eastern Restaurant   
25           Nightclub          Gas Station                 Baby Store   
35             Dog Run         Dessert Shop         Dim Sum Restaurant   
37    Asian Restaurant                 Café                Men's Store   
49         Yoga Studio     Doner Restaurant         Dim Sum Restaurant   
51               Motel         Dessert Shop         Dim Sum Restaurant   
55      Sandwich Place    Indian Restaurant       Fast Food Restaurant   
57    Department Store   Dim Sum Restaurant                      Diner   
59                Café           Restaurant           Sushi Restaurant   
65  Chinese Restaurant          Yoga Studio        Distribution Center   
69     Thai Restaurant        Grocery Store     Furniture / Home Store   
83          Playground          Yoga Studio        Distribution Center   
85          Playground          Yoga Studio                    Dog Run   
92                Café             Beer Bar                      Hotel   
98    Department Store         Dessert Shop         Dim Sum Restaurant   

      7th  Common Venue      8th  Common Venue    9th  Common Venue  \
9    Italian Restaurant        Bubble Tea Shop            Bookstore   
25           Restaurant            Candy Store                Diner   
35                Diner         Discount Store  Distribution Center   
37             Wine Bar  Vietnamese Restaurant          Pizza Place   
49                Diner         Discount Store  Distribution Center   
51                Diner         Discount Store  Distribution C

Borough  Cluster Labels  \
9                                 Downtown Toronto               0   
25                                Downtown Toronto               0   
35                           East YorkEast Toronto               0   
37                                    West Toronto               0   
49                                      North York               0   
51                                     Scarborough               0   
55                                      North York               0   
57                                      North York               0   
59                                      North York               0   
65                                     Scarborough               0   
69                                    West Toronto               0   
83                                 Central Toronto               0   
85                                     Scarborough               0   
92  Downtown TorontoStn A PO Boxes25 The Esplanade               0   
98                                       Etobicoke               0   

         1st  Common Venue   2nd  Common Venue           3rd  Common Venue  \
9              Coffee Shop      Clothing Store                        Café   
25           Grocery Store                Café                        Park   
35                    Park   Convenience Store               Metro Station   
37                     Bar         Coffee Shop                  Restaurant   
49                    Park              Bakery  Construction & Landscaping   
51     American Restaurant       Movie Theater                Skating Rink   
55      Italian Restaurant         Coffee Shop                  Restaurant   
57  Furniture / Home Store      Baseball Field                 Yoga Studio   
59        Ramen Restaurant         Coffee Shop                 Pizza Place   
65       Indian Restaurant           Pet Store       Vietnamese Restaurant   
69                     Bar                Café          Mexican Restaurant   
83                     Gym                Park                Tennis Court   
85                    Park              Bakery                 Coffee Shop   
92             Coffee Shop  Seafood Restaurant                  Restaurant   
98                   River                Park                     Dog Run   

     4th  Common Venue    5th  Common Venue          6th  Common Venue  \
9       Cosmetics Shop  Japanese Restaurant  Middle Eastern Restaurant   
25           Nightclub          Gas Station                 Baby Store   
35             Dog Run         Dessert Shop         Dim Sum Restaurant   
37    Asian Restaurant                 Café                Men's Store   
49         Yoga Studio     Doner Restaurant         Dim Sum Restaurant   
51               Motel         Dessert Shop         Dim Sum Restaurant   
55      Sandwich Place    Indian Restaurant       Fast Food Restaurant   
57    Department Store   Dim Sum Restaurant                      Diner   
59                Café           Restaurant           Sushi Restaurant   
65  Chinese Restaurant          Yoga Studio        Distribution Center   
69     Thai Restaurant        Grocery Store     Furniture / Home Store   
83          Playground          Yoga Studio        Distribution Center   
85          Playground          Yoga Studio                    Dog Run   
92                Café             Beer Bar                      Hotel   
98    Department Store         Dessert Shop         Dim Sum Restaurant   

      7th  Common Venue      8th  Common Venue    9th  Common Venue  \
9    Italian Restaurant        Bubble Tea Shop            Bookstore   
25           Restaurant            Candy Store                Diner   
35                Diner         Discount Store  Distribution Center   
37             Wine Bar  Vietnamese Restaurant          Pizza Place   
49                Diner         Discount Store  Distribution Center   
51                Diner         Discount Store  Distribution C

In [35]:
# Cluster 2
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels  \
0                                         North York               1   
1                                         North York               1   
2                                   Downtown Toronto               1   
3                                         North York               1   
4       Queen's Park / Ontario Provincial Government               1   
5                                          Etobicoke               1   
6                                        Scarborough               1   
7                                         North York               1   
8                                          East York               1   
10                                        North York               1   
11                                         Etobicoke               1   
12                                       Scarborough               1   
13                                        North York               1   
14                                         East York               1   
15                                  Downtown Toronto               1   
16                                              York               1   
17                                         Etobicoke               1   
18                                       Scarborough               1   
19                                      East Toronto               1   
20                                  Downtown Toronto               1   
21                                              York               1   
22                                       Scarborough               1   
23                                         East York               1   
24                                  Downtown Toronto               1   
26                                       Scarborough               1   
27                                        North York               1   
28                                        North York               1   
29                                         East York               1   
30                                  Downtown Toronto               1   
31                                      West Toronto               1   
32                                       Scarborough               1   
33                                        North York               1   
34                                        North York               1   
36                                  Downtown Toronto               1   
38                                       Scarborough               1   
39                                        North York               1   
40                                        North York               1   
41                                      East Toronto               1   
42                                  Downtown Toronto               1   
43                                      West Toronto               1   
44                                       Scarborough               1   
45                                        North York               1   
46                                        North York               1   
47                                      East Toronto               1   
48                                  Downtown Toronto               1   
50                                        North York               1   
52                                        North York               1   
53                                        North York               1   
56                                              York               1   
58                                       Scarborough               1   
60                                        North York               1   
61                                   Central Toronto               1   
62                                   Central Toronto               1   
63                                              York               1   
64                                              York               1   
66           

Borough  Cluster Labels  \
0                                         North York               1   
1                                         North York               1   
2                                   Downtown Toronto               1   
3                                         North York               1   
4       Queen's Park / Ontario Provincial Government               1   
5                                          Etobicoke               1   
6                                        Scarborough               1   
7                                         North York               1   
8                                          East York               1   
10                                        North York               1   
11                                         Etobicoke               1   
12                                       Scarborough               1   
13                                        North York               1   
14                                         East York               1   
15                                  Downtown Toronto               1   
16                                              York               1   
17                                         Etobicoke               1   
18                                       Scarborough               1   
19                                      East Toronto               1   
20                                  Downtown Toronto               1   
21                                              York               1   
22                                       Scarborough               1   
23                                         East York               1   
24                                  Downtown Toronto               1   
26                                       Scarborough               1   
27                                        North York               1   
28                                        North York               1   
29                                         East York               1   
30                                  Downtown Toronto               1   
31                                      West Toronto               1   
32                                       Scarborough               1   
33                                        North York               1   
34                                        North York               1   
36                                  Downtown Toronto               1   
38                                       Scarborough               1   
39                                        North York               1   
40                                        North York               1   
41                                      East Toronto               1   
42                                  Downtown Toronto               1   
43                                      West Toronto               1   
44                                       Scarborough               1   
45                                        North York               1   
46                                        North York               1   
47                                      East Toronto               1   
48                                  Downtown Toronto               1   
50                                        North York               1   
52                                        North York               1   
53                                        North York               1   
56                                              York               1   
58                                       Scarborough               1   
60                                        North York               1   
61                                   Central Toronto               1   
62                                   Central Toronto               1   
63                                              York               1   
64                                              York               1   
66           

In [36]:
# Cluster 3
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels     1st  Common Venue   2nd  Common Venue  \
90  Scarborough               2  Fast Food Restaurant  Chinese Restaurant   

   3rd  Common Venue 4th  Common Venue 5th  Common Venue 6th  Common Venue  \
90          Pharmacy              Bank    Sandwich Place       Pizza Place   

   7th  Common Venue 8th  Common Venue 9th  Common Venue 10th  Common Venue  
90     Grocery Store       Coffee Shop    Breakfast Spot         Nail Salon

Borough  Cluster Labels     1st  Common Venue   2nd  Common Venue  \
90  Scarborough               2  Fast Food Restaurant  Chinese Restaurant   

   3rd  Common Venue 4th  Common Venue 5th  Common Venue 6th  Common Venue  \
90          Pharmacy              Bank    Sandwich Place       Pizza Place   

   7th  Common Venue 8th  Common Venue 9th  Common Venue 10th  Common Venue  
90     Grocery Store       Coffee Shop    Breakfast Spot         Nail Salon

In [37]:
# Cluster 4
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st  Common Venue    2nd  Common Venue  \
99  Downtown Toronto               3       Coffee Shop  Japanese Restaurant   

   3rd  Common Venue 4th  Common Venue 5th  Common Venue 6th  Common Venue  \
99           Gay Bar  Sushi Restaurant        Restaurant               Pub   

           7th  Common Venue 8th  Common Venue 9th  Common Venue  \
99  Mediterranean Restaurant       Men's Store   Bubble Tea Shop   

   10th  Common Venue  
99              Hotel

Borough  Cluster Labels 1st  Common Venue    2nd  Common Venue  \
99  Downtown Toronto               3       Coffee Shop  Japanese Restaurant   

   3rd  Common Venue 4th  Common Venue 5th  Common Venue 6th  Common Venue  \
99           Gay Bar  Sushi Restaurant        Restaurant               Pub   

           7th  Common Venue 8th  Common Venue 9th  Common Venue  \
99  Mediterranean Restaurant       Men's Store   Bubble Tea Shop   

   10th  Common Venue  
99              Hotel

In [38]:
# Cluster 5
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st  Common Venue 2nd  Common Venue  \
54  East Toronto               4              Café       Coffee Shop   

   3rd  Common Venue    4th  Common Venue 5th  Common Venue 6th  Common Venue  \
54           Brewery  American Restaurant            Bakery       Yoga Studio   

   7th  Common Venue 8th  Common Venue 9th  Common Venue 10th  Common Venue  
54               Bar  Stationery Store       Fish Market     Ice Cream Shop

Borough  Cluster Labels 1st  Common Venue 2nd  Common Venue  \
54  East Toronto               4              Café       Coffee Shop   

   3rd  Common Venue    4th  Common Venue 5th  Common Venue 6th  Common Venue  \
54           Brewery  American Restaurant            Bakery       Yoga Studio   

   7th  Common Venue 8th  Common Venue 9th  Common Venue 10th  Common Venue  
54               Bar  Stationery Store       Fish Market     Ice Cream Shop

# Conclusion:

Analyzing the clusters and the frequency we found that the neighborhoods in which you could have an office with nearby services are the following neighborhoods:

----Bathurst Manor, Wilson Heights, Downsview North---- VENUES:      
                       Bank  freq 0.11,
                Coffee Shop  freq 0.11,
  Middle Eastern Restaurant  freq 0.05,
                 Restaurant  freq 0.05,
                Gas Station  freq 0.05,
                Bridal Shop  freq 0.05,
             Ice Cream Shop  freq 0.05,
                Supermarket  freq 0.05,
              Deli / Bodega  freq 0.05,
             Sandwich Place  freq 0.05

----Bayview Village---- VENUES:
                        Café  freq 0.25,
                       Bank  freq 0.25,
         Chinese Restaurant  freq 0.25,
        Japanese Restaurant   freq 0.25,
          
----Clarks Corners, Tam O'Shanter, Sullivan---- VENUES:
                     Pizza Place freq 0.14,
  Fast Food Restaurant  freq 0.07,
   Fried Chicken Joint  freq 0.07,
                  Bank  freq 0.07,
    Italian Restaurant  freq 0.07,
    Chinese Restaurant  freq 0.07,
       Thai Restaurant  freq 0.07,
           Gas Station  freq 0.07,
          Intersection  freq 0.07,
         Shopping Mall  freq 0.07

----Downsview West---- VENUES                       
              Grocery Store freq 0.33,
                       Park freq 0.17,
                       Bank freq 0.17,
              Shopping Mall freq 0.17,
                      Hotel freq 0.17
   